# Read National Water Model (NWM) model data from Zarr

In [1]:
%matplotlib inline

from dask.distributed import Client, progress, LocalCluster
from dask_kubernetes import KubeCluster
import xarray as xr
import hvplot.xarray
import geoviews as gv
import cartopy.crs as ccrs
import s3fs

In [2]:
cluster = KubeCluster()

In [3]:
cluster.scale(25);

In [4]:
cluster

In [5]:
client = Client(cluster)

In [6]:
# jetstream s3
# url='https://iu.jetstream-cloud.org:8080'
# fs = s3fs.S3FileSystem(client_kwargs=dict(endpoint_url=url), anon=True)
# s3map = s3fs.S3Map('rsignell/nwm/test_week', s3=fs)

In [7]:
# AWS s3
fs = s3fs.S3FileSystem(anon=True)   # set "anon=True" to access public read buckets
s3map = s3fs.S3Map('esip-pangeo/pangeo/NWM/short_term_forcing', s3=fs)

In [8]:
ds = xr.open_zarr(s3map)

In [9]:
ds

<xarray.Dataset>
Dimensions:   (time: 168, x: 4608, y: 3840)
Coordinates:
  * time      (time) datetime64[ns] 2018-04-01T01:00:00 ... 2018-04-08
  * x         (x) float64 -2.304e+06 -2.303e+06 ... 2.302e+06 2.303e+06
  * y         (y) float64 -1.92e+06 -1.919e+06 ... 1.918e+06 1.919e+06
Data variables:
    LWDOWN    (time, y, x) float64 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    PSFC      (time, y, x) float64 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    Q2D       (time, y, x) float64 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    RAINRATE  (time, y, x) float32 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    SWDOWN    (time, y, x) float64 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    T2D       (time, y, x) float64 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    U2D       (time, y, x) float64 dask.array<shape=(168, 3840, 4608), chunksize=(168, 384, 288)>
    V2D   

In [10]:
var='T2D'

In [11]:
ds[var].nbytes/1.e9

23.78170368

In [12]:
uvar = ds[var].max(dim='time').persist()
progress(uvar)

VBox()

In [13]:
from geoviews import tile_sources as gvts
import panel as pn

In [14]:
base_map = gvts.OSM

In [15]:
ds[var].esri_pe_string

'PROJCS["Sphere_Lambert_Conformal_Conic",GEOGCS["GCS_Sphere",DATUM["D_Sphere",SPHEROID["Sphere",6370000.0,0.0]],PRIMEM["Greenwich",0.0],UNIT["Degree",0.0174532925199433]],PROJECTION["Lambert_Conformal_Conic"],PARAMETER["false_easting",0.0],PARAMETER["false_northing",0.0],PARAMETER["central_meridian",-97.0],PARAMETER["standard_parallel_1",30.0],PARAMETER["standard_parallel_2",60.0],PARAMETER["latitude_of_origin",40.0000076294],UNIT["Meter",1.0]];-35691800 -29075200 126180232.640845;-100000 10000;-100000 10000;0.001;0.001;0.001;IsHighPrecision'

In [16]:
globe = ccrs.Globe(ellipse='sphere', semimajor_axis=6370000.0)
lat0 = 40.0000076294
lat1 = 30.
lat2 = 60.
lon0 = -97.0
crs = ccrs.LambertConformal(central_latitude=lat0, central_longitude=lon0,
                            standard_parallels=(lat1,lat2), globe=globe)

In [17]:
mesh = uvar.hvplot(x='x', y='y', rasterize=True, cmap='viridis', crs=crs, width=800, height=550)

In [18]:
overlay = (base_map * mesh.opts(alpha=0.7)).opts(active_tools=['wheel_zoom', 'pan'])

In [19]:
overlay

:DynamicMap   []
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (T2D)

In [20]:
%%time
ds1d = ds[var][:,2000,2000]
display(ds1d.hvplot())

:Curve   [time]   (T2D)

CPU times: user 180 ms, sys: 24 ms, total: 204 ms
Wall time: 1.35 s
